In [1]:
from google_play_scraper import app, Sort, reviews_all

import pandas as pd

import numpy as np

import re

import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import classification_report

In [11]:
#ID Market
id_reviews = reviews_all(
    'com.twitter.android',
    sleep_milliseconds=0, # defaults to 0
    lang='id', # defaults to 'en'
    country='id', # defaults to 'us'
    sort=Sort.NEWEST, # defaults to Sort.MOST_RELEVANT
)

In [12]:
# Convert the list of reviews to a DataFrame
df = pd.DataFrame(id_reviews)

In [13]:
# Export the DataFrame to a CSV file
df.to_csv('x_reviews.csv', index=False)  # Specify the file name

In [3]:
df_x = pd.read_csv('x_reviews.csv')

C:\Users\USER\AppData\Local\Temp\ipykernel_15844\2452563388.py:1: DtypeWarning: Columns (8,9) have mixed types. Specify dtype option on import or set low_memory=False.
  df_x = pd.read_csv('x_reviews.csv')


In [4]:
df_x.head(10)

reviewId                      userName  \
0  aa9c71d1-3714-4011-87a7-762befb3110d                  Awsvrtx Brow   
1  f6dcb77b-1ec5-4a55-aac4-9fd5a6827b3d           Nikodemus Wambosene   
2  267d16e5-9364-46fb-9dea-50fb11529a0c                   Alya Zafira   
3  0d7dd1f6-80f1-45a1-b604-0bf4f94ae4e3                     Zalman Yu   
4  1f236d07-5c4f-4a88-bc87-f33dfd826d22                        al ber   
5  73770313-b988-4583-879a-dc1b35d09d10                   Sami Basuki   
6  f0213380-c1c6-4c73-b8f5-8b0e373c68b7  MUHAMMAD Salman Al-Parisi 03   
7  6ab694d6-58d3-4096-b024-fc180151e797           Mohammad Ekasaputra   
8  020be1b8-a382-4c31-ac8b-8161bf9f0b1b             Noorkhadijah Ijah   
9  8db11c1b-acd4-47db-9c93-b0966bdbcf28                           Ara   

                                           userImage  \
0  https://play-lh.googleusercontent.com/a/ACg8oc...   
1  https://play-lh.googleusercontent.com/a-/ALV-U...   
2  https://play-lh.googleusercontent.com/a-/ALV-U...   
3  https://play-lh.googleusercontent.com/a-/ALV-U...   
4  https://play-lh.googleusercontent.com/a/ACg8oc...   
5  https://play-lh.googleusercontent.com/a-/ALV-U...   
6  https://play-lh.googleusercontent.com/a-/ALV-U...   
7  https://play-lh.googleusercontent.com/a-/ALV-U...   
8  https://play-lh.googleusercontent.com/a-/ALV-U...   
9  https://play-lh.googleusercontent.com/a-/ALV-U...   

                                             content  score  thumbsUpCount  \
0  Kesalahan teknis saat membuat akun baru, itu s...      3              0   
1                                       Bagus sekali      5              0   
2                             bagusan jg ver yg dulu      1              0   
3                                  Tidak bisa daftar      1              0   
4  Aplikasi terburuk yang pernah ada, akunku dibl...      1              0   
5               mantap manga dan manhua, manhwa LGBT      5              0   
6                                       Gajelas beut      1              0   
7                                        apk gajelas      1              0   
8  ini kenapa ya, saya bikin akun Twitter terus a...      1              0   
9  I've uninstalled it twice after years of downl...      1              0   

  reviewCreatedVersion                   at replyContent repliedAt  
0     10.7.0-release.0  2023-10-16 17:17:17          NaN       NaN  
1                  NaN  2023-10-16 17:10:35          NaN       NaN  
2                  NaN  2023-10-16 17:09:40          NaN       NaN  
3                  NaN  2023-10-16 16:26:50          NaN       NaN  
4                  NaN  2023-10-16 16:20:55          NaN       NaN  
5    10.11.0-release.0  2023-10-16 16:13:57          NaN       NaN  
6                  NaN  2023-10-16 16:05:19          NaN       NaN  
7                  NaN  2023-10-16 15:32:37          NaN       NaN  
8                  NaN  2023-10-16 15:26:46          NaN       NaN  
9     10.1.0-release.0  2023-10-16 14:58:40          NaN       NaN

In [5]:
# Convert data types of the columns
df_x['reviewId'] = df_x['reviewId'].astype(str)
df_x['userName'] = df_x['userName'].astype(str)
df_x['userImage'] = df_x['userImage'].astype(str)
df_x['content'] = df_x['content'].astype(str)
df_x['score'] = df_x['score'].astype(int)
df_x['thumbsUpCount'] = df_x['thumbsUpCount'].astype(int)
df_x['reviewCreatedVersion'] = df_x['reviewCreatedVersion'].astype(str)
df_x['at'] = pd.to_datetime(df_x['at'])
df_x['replyContent'] = df_x['replyContent'].astype(str)
df_x['repliedAt'] = pd.to_datetime(df_x['repliedAt'])


In [6]:
column_dtypes = df_x.dtypes
print(column_dtypes)

reviewId                        object
userName                        object
userImage                       object
content                         object
score                            int32
thumbsUpCount                    int32
reviewCreatedVersion            object
at                      datetime64[ns]
replyContent                    object
repliedAt               datetime64[ns]
dtype: object


In [7]:
#Review Selection
# Convert 'at' column to datetime format
df_x['at'] = pd.to_datetime(df_x['at'])

# Set the start and end date range
start_date = pd.to_datetime('2022-10-17')
end_date = pd.to_datetime('2023-10-17')

# Filter the DataFrame for data within the specified date range
df_ytd = df_x[(df_x['at'] >= start_date) & (df_x['at'] <= end_date)]

In [8]:
num_records = len(df_ytd)
print("Number of records in df_ytd:", num_records)

Number of records in df_ytd: 42523


In [9]:
start_date = df_ytd['at'].min()
end_date = df_ytd['at'].max()

print("Start Date:", start_date)
print("End Date:", end_date)


Start Date: 2022-10-17 00:17:38
End Date: 2023-10-16 17:17:17


In [10]:
df_textPreprocessing = df_ytd.copy()

In [11]:
#Manual Labelling

# Initialize the label column
df_textPreprocessing['label'] = None

# Iterate over each row in the DataFrame
for index, row in df_textPreprocessing.iterrows():
    review = row['content']
    rating = row['score']
    
    # Manually assign a label based on the rating
    if rating in [1, 2]:
        label = 'Negative'
    elif rating in [4, 5]:
        label = 'Positive'
    else:
        label = 'Neutral'
    
    # Update the 'label' column for the current row
    df_textPreprocessing.at[index, 'label'] = label


In [12]:
# Delete rows with "Neutral" label
df_textPreprocessing = df_textPreprocessing[df_textPreprocessing['label'] != 'Neutral']

# Remove neutral ratings
df_textPreprocessing = df_textPreprocessing[~df_textPreprocessing['score'].isin([3])]


In [14]:
num_records = len(df_textPreprocessing)
print("Number of records in df_textPreprocessing:", num_records)

Number of records in df_textPreprocessing: 40462


In [30]:
df_textPreprocessing.tail(10)

reviewId             userName  \
42512  3140f30b-12b7-4076-8338-9048c95c1090        Cakra Mentari   
42513  3a50f295-4fe3-4e41-8994-6c3cec6cef0f  JUST TAKE YOUR TIME   
42514  9d3590eb-f208-4ee5-8eeb-13c0d9148e8e        Defi Novianty   
42515  b39c7ec1-71fc-48fa-9a5b-f2ebde932f24        Budi Setiawan   
42516  b71ba39e-0725-4833-9acb-3cdc437756f0       Muhammad Rafli   
42517  7f0bb447-5d64-42ae-b1e0-0f51f65d057c           Ivan Sigit   
42518  4a53d9af-0d69-4939-ad66-3ccefef8b6aa          Ina Herlina   
42519  1d6aab76-046d-4638-958a-f960d197c888         Aris Mawardi   
42520  f2c60c56-f621-4fea-8493-e26219a72fa4         Asep Riadi12   
42522  d961babe-dae7-4bfb-94cb-ea9a5155fc63           Tlc Mobile   

                                               userImage  \
42512  https://play-lh.googleusercontent.com/a-/ALV-U...   
42513  https://play-lh.googleusercontent.com/a-/ALV-U...   
42514  https://play-lh.googleusercontent.com/a-/ALV-U...   
42515  https://play-lh.googleusercontent.com/a-/ALV-U...   
42516  https://play-lh.googleusercontent.com/a-/ALV-U...   
42517  https://play-lh.googleusercontent.com/a-/ALV-U...   
42518  https://play-lh.googleusercontent.com/a/ACg8oc...   
42519  https://play-lh.googleusercontent.com/a-/ALV-U...   
42520  https://play-lh.googleusercontent.com/a-/ALV-U...   
42522  https://play-lh.googleusercontent.com/a/ACg8oc...   

                                    content  score  thumbsUpCount  \
42512                                     👍      5              0   
42513                  Twitter the best sih      5              0   
42514             saya senang dgn situs ini      2              0   
42515                               Mantabs      5              0   
42516  mau daftar tapi ga dikasih kode anjg      1              0   
42517         Sangat amat bermanfaat sekali      5              0   
42518                          Keren banget      5              0   
42519                                 Bagus      5              0   
42520                                   Oke      5              0   
42522                           Is the best      5              0   

      reviewCreatedVersion                  at replyContent repliedAt  \
42512                  nan 2022-10-17 05:20:47          nan       NaT   
42513     9.63.0-release.0 2022-10-17 04:15:45          nan       NaT   
42514     9.63.0-release.0 2022-10-17 04:11:35          nan       NaT   
42515     9.63.0-release.0 2022-10-17 03:48:48          nan       NaT   
42516     9.63.0-release.0 2022-10-17 03:11:02          nan       NaT   
42517     9.63.0-release.0 2022-10-17 02:46:13          nan       NaT   
42518     9.62.0-release.0 2022-10-17 02:26:02          nan       NaT   
42519     9.63.0-release.0 2022-10-17 01:31:28          nan       NaT   
42520     9.62.0-release.0 2022-10-17 01:26:53          nan       NaT   
42522     9.63.0-release.0 2022-10-17 00:17:38          nan       NaT   

          label  
42512  Positive  
42513  Positive  
42514  Negative  
42515  Positive  
42516  Negative  
42517  Positive  
42518  Positive  
42519  Positive  
42520  Positive  
42522  Positive

In [28]:
# Assuming you have a DataFrame named df

# Concatenate the content column into one paragraph
single_paragraph = ' '.join(df_textPreprocessing['content'].tolist())

# Print the single paragraph
print(single_paragraph)


Bagus sekali bagusan jg ver yg dulu Tidak bisa daftar Aplikasi terburuk yang pernah ada, akunku diblokir tanpa sebab👎👎👎 mantap manga dan manhua, manhwa LGBT Gajelas beut apk gajelas ini kenapa ya, saya bikin akun Twitter terus ada daftaran nomor. Tapi udah dimasukkan nomor nya malah valid/tidak sah. Perbaiki lagi ya I've uninstalled it twice after years of downloading, but this time the apk has an error. Please fix it quickly Sangat bermanfaat sekali 😀 App gak jelas. Mau masuk pakek akun lama gak bisa katanya belum terdaftar. Mau daftar lagi katanya nope gak bisa di daftarkan gak jelas alasannya please more updates, why my dm still limited? cause iam not premium or else?? Aplikasi nya sangat bagus Videonya gabisa diputer lagi. Gimana sih Mau daftar susahnya minta ampun dah.. X knapa ini kok jadi gangguan gini Aplikasi tolol Aku gak terlalu suka apk ny,setelah diganti jadi x,Twitter jadi jlk bgt Lama² gak jelas bgt nih aplikasi !!! Akun ke suspend terus,baru scroll sedikit udah ada kete

In [29]:
# Misalnya, single_paragraph adalah paragraf yang ingin Anda pisah
words = single_paragraph.split()  # Memisahkan kata-kata berdasarkan spasi
print(words)


['Bagus', 'sekali', 'bagusan', 'jg', 'ver', 'yg', 'dulu', 'Tidak', 'bisa', 'daftar', 'Aplikasi', 'terburuk', 'yang', 'pernah', 'ada,', 'akunku', 'diblokir', 'tanpa', 'sebab👎👎👎', 'mantap', 'manga', 'dan', 'manhua,', 'manhwa', 'LGBT', 'Gajelas', 'beut', 'apk', 'gajelas', 'ini', 'kenapa', 'ya,', 'saya', 'bikin', 'akun', 'Twitter', 'terus', 'ada', 'daftaran', 'nomor.', 'Tapi', 'udah', 'dimasukkan', 'nomor', 'nya', 'malah', 'valid/tidak', 'sah.', 'Perbaiki', 'lagi', 'ya', "I've", 'uninstalled', 'it', 'twice', 'after', 'years', 'of', 'downloading,', 'but', 'this', 'time', 'the', 'apk', 'has', 'an', 'error.', 'Please', 'fix', 'it', 'quickly', 'Sangat', 'bermanfaat', 'sekali', '😀', 'App', 'gak', 'jelas.', 'Mau', 'masuk', 'pakek', 'akun', 'lama', 'gak', 'bisa', 'katanya', 'belum', 'terdaftar.', 'Mau', 'daftar', 'lagi', 'katanya', 'nope', 'gak', 'bisa', 'di', 'daftarkan', 'gak', 'jelas', 'alasannya', 'please', 'more', 'updates,', 'why', 'my', 'dm', 'still', 'limited?', 'cause', 'iam', 'not', 'pr